In [2]:
#Import all dependencies
import pandas as pd
import matplotlib.pyplot as plt
import sklearn as skl
import tensorflow as tf

import hvplot.pandas
from sklearn.cluster import KMeans
import joblib

In [3]:
#Read in our movie data
movies = pd.read_csv(r"ml-25m (2)\ml-25m\movies.csv")
movies.head()


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [4]:
#The following code will create columns for each genre which specify whether each movie is in that genre or not
#Create a dictionary to store our genres
genres = {}


In [5]:
#Split the genre column from the movie data into lists and store in a dictionary
for index, row in movies.iterrows():
    genres[row["movieId"]] = row["genres"].split("|")

In [6]:
#Create our list of genres for our genre dictionary
genre_list = ["Action",
"Adventure",
"Animation",
"Children's",
"Comedy",
"Crime",
"Documentary",
"Drama",
"Fantasy",
"Film-Noir",
"Horror",
"Musical",
"Mystery",
"Romance",
"Sci-Fi",
"Thriller",
"War",
"Western",
"(no genres listed)"]

In [7]:
#Create a list that will store each genre column
my_list = []

In [8]:
#Fill all of the genre columns with 1 for "yes" or 0 for "no"
for genre in genre_list:
    my_list = []
    for index in movies.index:
        movie = movies["movieId"][index]
        if genre in genres[movie]:
            my_list.append(1)
        else:
            my_list.append(0)
    movies[genre] = my_list

In [9]:
#Clean up the movies DataFrame
movies = movies.drop(columns = ["genres", "title"])
movies.head()

movieId  Action  Adventure  Animation  Children's  Comedy  Crime  \
0        1       0          1          1           0       1      0   
1        2       0          1          0           0       0      0   
2        3       0          0          0           0       1      0   
3        4       0          0          0           0       1      0   
4        5       0          0          0           0       1      0   

   Documentary  Drama  Fantasy  Film-Noir  Horror  Musical  Mystery  Romance  \
0            0      0        1          0       0        0        0        0   
1            0      0        1          0       0        0        0        0   
2            0      0        0          0       0        0        0        1   
3            0      1        0          0       0        0        0        1   
4            0      0        0          0       0        0        0        0   

   Sci-Fi  Thriller  War  Western  (no genres listed)  
0       0         0    0        0                   0  
1       0         0    0        0                   0  
2       0         0    0        0                   0  
3       0         0    0        0                   0  
4       0         0    0        0                   0

In [10]:
#The following csv is not used in the current iteration of our model, but could be used to increase its complexity
#Read in tag movie metadata
tag_names = pd.read_csv(r"ml-25m (2)/ml-25m/genome-tags.csv")
tag_list = tag_names["tagId"]
tag_scores = pd.read_csv(r"ml-25m (2)\ml-25m\genome-scores.csv")
tag_scores.head()

movieId  tagId  relevance
0        1      1    0.02875
1        1      2    0.02375
2        1      3    0.06250
3        1      4    0.07575
4        1      5    0.14075

In [11]:
#Add tag data to the movie data through merge, thereby assigning tag_scores to their movies
merged_df = pd.merge(movies,tag_scores, on = ["movieId"], how = "left")

In [12]:
#Invert rows and columns so that tags are columns, preserving only movieId, tagId, and relevance
pivot_df = merged_df.pivot(index = "movieId", columns = "tagId", values = "relevance")

In [13]:
#Put this inverted data into the movie DataFrame
movies_with_tags = pd.merge(movies, pivot_df, left_on = "movieId", right_index = True, how = "left")

In [14]:
#Drop fully null columns
movies_with_tags = movies_with_tags.dropna(axis=1,how = 'all')
movies_with_tags.head()

movieId  Action  Adventure  Animation  Children's  Comedy  Crime  \
0        1       0          1          1           0       1      0   
1        2       0          1          0           0       0      0   
2        3       0          0          0           0       1      0   
3        4       0          0          0           0       1      0   
4        5       0          0          0           0       1      0   

   Documentary  Drama  Fantasy  ...   1119.0   1120.0   1121.0   1122.0  \
0            0      0        1  ...  0.04050  0.01425  0.03050  0.03500   
1            0      0        1  ...  0.05250  0.01575  0.01250  0.02000   
2            0      0        0  ...  0.06275  0.01950  0.02225  0.02300   
3            0      1        0  ...  0.05325  0.02800  0.01675  0.03875   
4            0      0        0  ...  0.05350  0.02050  0.01425  0.02550   

    1123.0   1124.0   1125.0   1126.0   1127.0   1128.0  
0  0.14125  0.05775  0.03900  0.02975  0.08475  0.02200  
1  0.12225  0.03275  0.02100  0.01100  0.10525  0.01975  
2  0.12200  0.03475  0.01700  0.01800  0.09100  0.01775  
3  0.18200  0.07050  0.01625  0.01425  0.08850  0.01500  
4  0.19225  0.02675  0.01625  0.01300  0.08700  0.01600  

[5 rows x 1148 columns]

In [15]:
#Save the movies_with_tags DataFrame to csv for future use
movies_with_tags.to_csv(r"ml-25m (2)\ml-25m\movies_with_tags.csv")

In [16]:
#Read in customer rating data
ratings = pd.read_csv(r"ml-25m (2)\ml-25m\ratings.csv")
ratings.head()

userId  movieId  rating   timestamp
0       1      296     5.0  1147880044
1       1      306     3.5  1147868817
2       1      307     5.0  1147868828
3       1      665     5.0  1147878820
4       1      899     3.5  1147868510

In [17]:
#Join movie and ratings data so that each rating is paired with the movie metadata
ratings = ratings.join(movies.set_index("movieId"), on = "movieId", how = "left")
ratings = ratings.drop(columns=["Children's"])
ratings.head()

userId  movieId  rating   timestamp  Action  Adventure  Animation  Comedy  \
0       1      296     5.0  1147880044       0          0          0       1   
1       1      306     3.5  1147868817       0          0          0       0   
2       1      307     5.0  1147868828       0          0          0       0   
3       1      665     5.0  1147878820       0          0          0       1   
4       1      899     3.5  1147868510       0          0          0       1   

   Crime  Documentary  ...  Film-Noir  Horror  Musical  Mystery  Romance  \
0      1            0  ...          0       0        0        0        0   
1      0            0  ...          0       0        0        0        0   
2      0            0  ...          0       0        0        0        0   
3      0            0  ...          0       0        0        0        0   
4      0            0  ...          0       0        1        0        1   

   Sci-Fi  Thriller  War  Western  (no genres listed)  
0       0         1    0        0                   0  
1       0         0    0        0                   0  
2       0         0    0        0                   0  
3       0         0    1        0                   0  
4       0         0    0        0                   0  

[5 rows x 22 columns]

In [18]:
#Replace zeroes in the ratings DataFrame with null values so that they will not affect our aggregate calculations
genre_columns = ['Action', 'Adventure',
       'Animation', 'Comedy', 'Crime', 'Documentary', 'Drama',
       'Fantasy', 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance',
       'Sci-Fi', 'Thriller', 'War', 'Western', '(no genres listed)']

for genre in genre_columns:
    ratings[genre] = ratings[genre]*ratings["rating"]
    ratings[genre] = ratings[genre].replace(0,float('nan'))

In [19]:
#Create a DataFrame that contains users' average ratings by genre
weighted_ratings = ratings.groupby("userId").mean().drop(columns=["movieId", "timestamp", "rating"])
weighted_ratings = weighted_ratings.fillna(0)
weighted_ratings.head()

Action  Adventure  Animation    Comedy     Crime  Documentary  \
userId                                                                    
1       4.125000   3.727273   4.000000  3.869565  4.062500     2.000000   
2       3.696970   3.906667   3.617647  3.317460  3.138889     0.000000   
3       3.640719   3.689394   3.980000  3.454545  3.886364     3.166667   
4       3.186207   3.074561   3.467742  3.611111  3.972973     4.100000   
5       3.722222   3.857143   3.750000  3.571429  4.142857     0.000000   

           Drama   Fantasy  Film-Noir    Horror   Musical   Mystery   Romance  \
userId                                                                          
1       3.867925  3.600000        3.5  3.500000  3.700000  3.500000  4.166667   
2       3.571429  3.982759        0.0  4.000000  3.272727  3.687500  3.161765   
3       3.890086  3.737179        4.3  3.544444  3.583333  3.891667  3.533333   
4       3.744898  2.833333        0.0  3.150000  3.642857  3.805556  3.450000   
5       3.822222  3.500000        0.0  4.666667  3.714286  4.714286  3.550000   

          Sci-Fi  Thriller       War   Western  (no genres listed)  
userId                                                              
1       3.700000  4.300000  3.900000  2.500000                 0.0  
2       4.017857  3.833333  3.433333  2.500000                 0.0  
3       3.696429  3.692469  3.692308  3.750000                 3.5  
4       3.164706  3.544643  3.333333  2.833333                 0.0  
5       4.090909  4.000000  4.500000  3.000000                 0.0

In [20]:
#Create a DataFrame that specifies how often a user rates a genre
ratings_counts = ratings.groupby("userId").count().drop(columns=["movieId", "timestamp"])
ratings_counts.head()

rating  Action  Adventure  Animation  Comedy  Crime  Documentary  \
userId                                                                     
1           70       4         11          2      23      8            1   
2          184      66         75         17      63     18            0   
3          656     334        198         50     176    132            3   
4          242     145        114         31      81     37            5   
5          101      18         21          4      49     14            0   

        Drama  Fantasy  Film-Noir  Horror  Musical  Mystery  Romance  Sci-Fi  \
userId                                                                         
1          53        5          1       1        5        4       18       5   
2          91       29          0       3       11        8       34      28   
3         232       78          5      45        6       60       60     224   
4          49       39          0      10        7       18       10      85   
5          45        8          0       3        7        7       20      11   

        Thriller  War  Western  (no genres listed)  
userId                                              
1              5    5        1                   0  
2             30   15        5                   0  
3            239   26        8                   1  
4             56    9        9                   0  
5             24    2        5                   0

In [32]:
#Turn these counts into weighted percentages like in StandardScaler so that they do not overweight the model
for genre in genre_columns:
    ratings_counts[genre] = 5*ratings_counts[genre]/ratings_counts["rating"]
ratings_counts.head()

rating    Action  Adventure  Animation    Comedy     Crime  \
userId                                                               
1           70  0.020408   0.056122   0.010204  0.117347  0.040816   
2          184  0.048736   0.055382   0.012553  0.046521  0.013292   
3          656  0.019403   0.011503   0.002905  0.010225  0.007668   
4          242  0.061898   0.048665   0.013233  0.034578  0.015795   
5          101  0.044113   0.051466   0.009803  0.120086  0.034310   

        Documentary     Drama   Fantasy  Film-Noir    Horror   Musical  \
userId                                                                   
1          0.005102  0.270408  0.025510   0.005102  0.005102  0.025510   
2          0.000000  0.067196  0.021414   0.000000  0.002215  0.008123   
3          0.000174  0.013478  0.004531   0.000290  0.002614  0.000349   
4          0.002134  0.020917  0.016648   0.000000  0.004269  0.002988   
5          0.000000  0.110283  0.019606   0.000000  0.007352  0.017155   

         Mystery   Romance    Sci-Fi  Thriller       War   Western  \
userId                                                               
1       0.020408  0.091837  0.025510  0.025510  0.025510  0.005102   
2       0.005907  0.025106  0.020676  0.022153  0.011076  0.003692   
3       0.003486  0.003486  0.013013  0.013884  0.001510  0.000465   
4       0.007684  0.004269  0.036285  0.023905  0.003842  0.003842   
5       0.017155  0.049015  0.026958  0.058818  0.004901  0.012254   

        (no genres listed)  
userId                      
1                 0.000000  
2                 0.000000  
3                 0.000058  
4                 0.000000  
5                 0.000000

In [22]:
#Combine our two new DataFrames to form the inputs for our model
weighted_ratings= pd.merge(ratings_counts,weighted_ratings, on = "userId", how = "left")
weighted_ratings = weighted_ratings.drop(columns=["rating"])
weighted_ratings.head()

Action_x  Adventure_x  Animation_x  Comedy_x   Crime_x  Documentary_x  \
userId                                                                          
1       0.285714     0.785714     0.142857  1.642857  0.571429       0.071429   
2       1.793478     2.038043     0.461957  1.711957  0.489130       0.000000   
3       2.545732     1.509146     0.381098  1.341463  1.006098       0.022866   
4       2.995868     2.355372     0.640496  1.673554  0.764463       0.103306   
5       0.891089     1.039604     0.198020  2.425743  0.693069       0.000000   

         Drama_x  Fantasy_x  Film-Noir_x  Horror_x  ...  Film-Noir_y  \
userId                                              ...                
1       3.785714   0.357143     0.071429  0.071429  ...          3.5   
2       2.472826   0.788043     0.000000  0.081522  ...          0.0   
3       1.768293   0.594512     0.038110  0.342988  ...          4.3   
4       1.012397   0.805785     0.000000  0.206612  ...          0.0   
5       2.227723   0.396040     0.000000  0.148515  ...          0.0   

        Horror_y  Musical_y  Mystery_y  Romance_y  Sci-Fi_y  Thriller_y  \
userId                                                                    
1       3.500000   3.700000   3.500000   4.166667  3.700000    4.300000   
2       4.000000   3.272727   3.687500   3.161765  4.017857    3.833333   
3       3.544444   3.583333   3.891667   3.533333  3.696429    3.692469   
4       3.150000   3.642857   3.805556   3.450000  3.164706    3.544643   
5       4.666667   3.714286   4.714286   3.550000  4.090909    4.000000   

           War_y  Western_y  (no genres listed)_y  
userId                                             
1       3.900000   2.500000                   0.0  
2       3.433333   2.500000                   0.0  
3       3.692308   3.750000                   3.5  
4       3.333333   2.833333                   0.0  
5       4.500000   3.000000                   0.0  

[5 rows x 36 columns]

In [23]:
#Run an elbow test to determine a minimum cluster number
inertia = []
k = list(range(1,50))

In [24]:
#Iterate through possible cluster numbers
for i in k:
    k_model = KMeans(n_clusters=i, random_state=1, n_init='auto')
    k_model.fit(weighted_ratings)
    inertia.append(k_model.inertia_)

In [25]:
#Store the inertia and elbow data
elbow_data = {"k": k, "inertia": inertia}
df_elbow = pd.DataFrame(elbow_data)

In [26]:
#Plot the elbow curve
df_elbow.hvplot.line(
    x="k", 
    y="inertia", 
    title="Elbow Curve", 
    xticks=k
)

:Curve   [k]   (inertia)

We can see here that the main crook of the "elbow" happens at around 10 or 11, but since our computing resources are capable of it we will use a higher n_cluster value of 20.

In [27]:
#Initiate the model
model = KMeans(n_clusters=20, random_state=1, n_init='auto')

#Fit the model to our data
model.fit(weighted_ratings)

#Make cluster predictions for the main model, so that we can examine cluster results to determine if our model is accurate
clusters = model.predict(weighted_ratings)

In [28]:
#Copy our DataFrame and attach cluster results
weighted_ratings_with_cluster = weighted_ratings.copy()
weighted_ratings_with_cluster["cluster"] = clusters

In [29]:
#View a DataFrame summarizing cluster results to scan for trends
weighted_ratings_with_cluster.groupby("cluster").mean()

Action_x  Adventure_x  Animation_x  Comedy_x   Crime_x  \
cluster                                                           
0        1.332477     1.068063     0.287927  1.720845  0.937480   
1        1.337403     1.027637     0.263560  1.814065  0.878220   
2        1.748773     1.093942     0.152213  1.190750  1.321043   
3        1.807910     1.422714     0.257130  1.620389  0.890469   
4        1.910802     1.144502     0.027276  1.417304  1.166348   
5        1.782016     1.492775     0.439728  1.786220  0.856675   
6        1.526133     1.519392     0.519632  2.131494  0.798863   
7        1.418736     1.204852     0.369149  1.931420  0.805466   
8        1.673068     0.993277     0.028384  1.291268  1.184195   
9        2.127293     1.750259     0.439483  1.304617  0.985827   
10       1.622355     1.271475     0.316814  1.667687  0.929454   
11       2.096844     1.550386     0.322000  1.307017  1.092675   
12       1.423578     1.160894     0.341210  1.611333  1.026774   
13       1.405131     1.540002     0.589849  2.192902  0.615608   
14       1.572938     1.473945     0.514046  1.852955  0.766498   
15       1.680427     1.326884     0.347061  1.904585  0.843499   
16       1.237998     1.022073     0.281553  2.030911  0.725220   
17       1.248522     1.179631     0.427606  1.849116  0.790387   
18       1.521164     1.535695     0.538179  1.971882  0.715696   
19       1.523461     1.182411     0.398234  1.574795  0.838505   

         Documentary_x   Drama_x  Fantasy_x  Film-Noir_x  Horror_x  ...  \
cluster                                                             ...   
0             0.095093  2.424850   0.517194     0.093498  0.317799  ...   
1             0.092582  2.329693   0.509881     0.076808  0.365723  ...   
2             0.020510  2.529834   0.388671     0.149855  0.354439  ...   
3             0.019980  1.831447   0.576692     0.024624  0.502808  ...   
4             0.019043  2.446973   0.301572     0.004592  0.307454  ...   
5             0.001359  1.995563   0.634868     0.000622  0.291477  ...   
6             0.006554  2.062951   0.587932     0.001815  0.188387  ...   
7             0.101235  2.210349   0.576485     0.001368  0.265239  ...   
8             0.027474  2.616071   0.340184     0.051476  0.361133  ...   
9             0.006108  2.151643   0.720387     0.005445  0.265918  ...   
10            0.002143  2.196316   0.569604     0.095570  0.350900  ...   
11            0.011036  2.282167   0.580144     0.001825  0.287874  ...   
12            0.018562  2.349148   0.578654     0.156611  0.359672  ...   
13            0.008033  1.658612   0.821643     0.006568  0.275036  ...   
14            0.002246  2.055843   0.759647     0.001889  0.349640  ...   
15            0.003384  1.996077   0.558160     0.003842  0.316111  ...   
16            0.056303  2.292983   0.501068     0.027039  0.313274  ...   
17            0.171426  2.351178   0.632263     0.009073  0.274469  ...   
18            0.003214  2.194878   0.695083     0.004251  0.016664  ...   
19            0.105152  2.233270   0.608881     0.046751  0.439615  ...   

         Film-Noir_y  Horror_y  Musical_y  Mystery_y  Romance_y  Sci-Fi_y  \
cluster                                                                     
0           4.177636  3.687621   3.773704   4.005919   3.866869  3.751097   
1           3.670535  2.910904   3.017741   3.402623   3.226741  3.039161   
2           4.154238  3.419428   0.200107   3.985712   3.720192  3.658091   
3           0.389818  2.502690   0.260395   3.502842   3.306658  3.614858   
4           0.081169  3.028957   0.341082   3.376939   3.594356  3.427542   
5           0.019822  3.901471   4.031302   4.033988   3.960726  3.853517   
6           0.028026  2.285420   3.570507   0.060013   3.781460  3.377898   
7           0.048604  3.240816   3.410384   3.653431   3.659112  3.488376   
8           0.806718  2.842719   0.362078   3.638404   3.582841  3.513463   
9           0.105405  2.699206   0.0

In [30]:
#Testing plot to check for visual trends between clusters
weighted_ratings_with_cluster.hvplot.scatter(
    x="Film-Noir_y", 
    y="Film-Noir_x", 
    by="cluster"
)

:NdOverlay   [cluster]
   :Scatter   [Film-Noir_y]   (Film-Noir_x)

In [31]:
#Tester prediction based on fake data to check that the model runs as expected
my_prediction=model.predict(pd.DataFrame({'Action_x':5/19, 'Adventure_x':5/19, 'Animation_x':5/19, 'Comedy_x':5/19, 'Crime_x':5/19,
       'Documentary_x':5/19, 'Drama_x':5/19, 'Fantasy_x':5/19, 'Film-Noir_x':5/19, 'Horror_x':5/19,
       'Musical_x':5/19, 'Mystery_x':5/19, 'Romance_x':5/19, 'Sci-Fi_x':5/19, 'Thriller_x':5/19,
       'War_x':5/19, 'Western_x':5/19, '(no genres listed)_x':5/19,'Action_y':2, 'Adventure_y':5,
       'Animation_y':2, 'Comedy_y':3, 'Crime_y':4, 'Documentary_y':4, 'Drama_y':4,
       'Fantasy_y':1, 'Film-Noir_y':1, 'Horror_y':2, 'Musical_y':0, 'Mystery_y':5, 'Romance_y':4,
       'Sci-Fi_y':2, 'Thriller_y':1, 'War_y':5, 'Western_y':5, '(no genres listed)_y':1}, index=[0]))
my_prediction

array([7])

In [33]:
#Export the model for use in Flask
joblib.dump(model, 'kmeans_model.pkl')

['kmeans_model.pkl']